# Solving a complex task with a multi-agent hierarchy


In [1]:
!pip install 'smolagents[litellm]' plotly geopandas shapely kaleido -q

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.9/42.9 kB 1.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 66.3/66.3 kB 4.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.4/56.4 kB 4.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.9/9.9 MB 77.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 149.8/149.8 kB 11.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 278.1/278.1 kB 20.5 MB/s eta 0:00:00


In [2]:
from huggingface_hub import notebook_login

notebook_login()

In [3]:
# We first make a tool to get the cargo plane transfer time.
import math
from typing import Optional, Tuple

from smolagents import tool


@tool
def calculate_cargo_travel_time(
    origin_coords: Tuple[float, float],
    destination_coords: Tuple[float, float],
    cruising_speed_kmh: Optional[float] = 750.0,  # Average speed for cargo planes
) -> float:
    """
    Calculate the travel time for a cargo plane between two points on Earth using great-circle distance.

    Args:
        origin_coords: Tuple of (latitude, longitude) for the starting point
        destination_coords: Tuple of (latitude, longitude) for the destination
        cruising_speed_kmh: Optional cruising speed in km/h (defaults to 750 km/h for typical cargo planes)

    Returns:
        float: The estimated travel time in hours

    Example:
        >>> # Chicago (41.8781° N, 87.6298° W) to Sydney (33.8688° S, 151.2093° E)
        >>> result = calculate_cargo_travel_time((41.8781, -87.6298), (-33.8688, 151.2093))
    """

    def to_radians(degrees: float) -> float:
        return degrees * (math.pi / 180)

    # Extract coordinates
    lat1, lon1 = map(to_radians, origin_coords)
    lat2, lon2 = map(to_radians, destination_coords)

    # Earth's radius in kilometers
    EARTH_RADIUS_KM = 6371.0

    # Calculate great-circle distance using the haversine formula
    dlon = lon2 - lon1
    dlat = lat2 - lat1

    a = (
        math.sin(dlat / 2) ** 2
        + math.cos(lat1) * math.cos(lat2) * math.sin(dlon / 2) ** 2
    )
    c = 2 * math.asin(math.sqrt(a))
    distance = EARTH_RADIUS_KM * c

    # Add 10% to account for non-direct routes and air traffic controls
    actual_distance = distance * 1.1

    # Calculate flight time
    # Add 1 hour for takeoff and landing procedures
    flight_time = (actual_distance / cruising_speed_kmh) + 1.0

    # Format the results
    return round(flight_time, 2)


print(calculate_cargo_travel_time((41.8781, -87.6298), (-33.8688, 151.2093)))

22.82


For the model provider, we use Together AI, one of the new [inference providers on the Hub](https://huggingface.co/blog/inference-providers)!

Regarding the GoogleSearchTool: this requires either having setup env variable `SERPAPI_API_KEY` and passing `provider="serpapi"` or having `SERPER_API_KEY` and passing `provider=serper`.

If you don't have any Serp API provider setup, you can use `DuckDuckGoSearchTool` but beware that it has a rate limit.

In [4]:
!pip install smolagents[telemetry] opentelemetry-sdk opentelemetry-exporter-otlp openinference-instrumentation-smolagents

INFO: pip is looking at multiple versions of opentelemetry-sdk to determine which version is compatible with other requirements. This could take a while.
INFO: pip is looking at multiple versions of opentelemetry-instrumentation to determine which version is compatible with other requirements. This could take a while.
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 88.0/88.0 kB 4.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.5/2.5 MB 39.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 301.2/301.2 kB 22.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 129.1/129.1 kB 10.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.7/134.7 kB 11.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.1/3.1 MB 83.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 331.1/331.1 kB 25.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 203.4/203.4 kB 16.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [ ]:
import base64
import os

os.environ["LANGFUSE_PUBLIC_KEY"] = ""
os.environ["LANGFUSE_SECRET_KEY"] = ""

LANGFUSE_PUBLIC_KEY = os.environ.get("LANGFUSE_PUBLIC_KEY")
LANGFUSE_SECRET_KEY = os.environ.get("LANGFUSE_SECRET_KEY")

if not LANGFUSE_PUBLIC_KEY or not LANGFUSE_SECRET_KEY:
    raise ValueError("Langfuse public or secret keys are missing!")

LANGFUSE_AUTH = base64.b64encode(f"{LANGFUSE_PUBLIC_KEY}:{LANGFUSE_SECRET_KEY}".encode()).decode()

# os.environ["OTEL_EXPORTER_OTLP_ENDPOINT"] = "https://cloud.langfuse.com/api/public/otel" # EU data region
os.environ["OTEL_EXPORTER_OTLP_ENDPOINT"] = "https://us.cloud.langfuse.com/api/public/otel" # US data region
os.environ["OTEL_EXPORTER_OTLP_HEADERS"] = f"Authorization=Basic {LANGFUSE_AUTH}"

print("Langfuse environment variables set successfully!")

Langfuse environment variables set successfully!


In [6]:
from opentelemetry.sdk.trace import TracerProvider

from openinference.instrumentation.smolagents import SmolagentsInstrumentor
from opentelemetry.exporter.otlp.proto.http.trace_exporter import OTLPSpanExporter
from opentelemetry.sdk.trace.export import SimpleSpanProcessor

trace_provider = TracerProvider()
trace_provider.add_span_processor(SimpleSpanProcessor(OTLPSpanExporter()))

SmolagentsInstrumentor().instrument(tracer_provider=trace_provider)

In [7]:
import os
from PIL import Image
from smolagents import CodeAgent, GoogleSearchTool, InferenceClientModel, VisitWebpageTool


model = InferenceClientModel(model_id="Qwen/Qwen2.5-Coder-32B-Instruct")

We can start with creating a baseline, simple agent to give us a simple report.

In [8]:
task = """Find all Harry Potter filming locations in the world, calculate the time to transfer via passenger plane to here (we're in Pune, 18.5204° N, 73.8567° E), and return them to me as a pandas dataframe.
Also give me some cricket stadiums if there are any nearby to the filming locations"""

In [ ]:
from google.colab import userdata
import os
os.environ["SERPAPI_API_KEY"] = ""

In [10]:
agent = CodeAgent(
    model=model,
    tools=[GoogleSearchTool(), VisitWebpageTool(), calculate_cargo_travel_time],
    additional_authorized_imports=["pandas"],
    max_steps=20,
)

In [11]:
result = agent.run(task)

╭──────────────────────────────────────────────────── New run ────────────────────────────────────────────────────╮
│                                                                                                                 │
│ Find all Harry Potter filming locations in the world, calculate the time to transfer via passenger plane to     │
│ here (we're in Pune, 18.5204° N, 73.8567° E), and return them to me as a pandas dataframe.                      │
│ Also give me some cricket stadiums if there are any nearby to the filming locations                             │
│                                                                                                                 │
╰─ InferenceClientModel - Qwen/Qwen2.5-Coder-32B-Instruct ────────────────────────────────────────────────────────╯

━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ Step 1 ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

─ Executing parsed code: ──────────────────────────────────────────────────────────────────────────────────────── 
  filming_locations_query_result = web_search(query="Harry Potter filming locations")                              
  print(filming_locations_query_result)                                                                            
 ─────────────────────────────────────────────────────────────────────────────────────────────────────────────────

Execution logs:
## Search Results
0. [Harry Potter filming locations guide - London - VisitBritain 
Shop](https://www.visitbritainshop.com/us/en/harry-potter-filming-locations-guide)
Source: visitbritainshop.com

Where was Harry Potter filmed in England? · Durham Cathedral · Alnwick Castle · Malham Cove, Skipton · New College,
Oxford · Lacock Abbey · Visit Lacock Abbey ...

1. [Top Sights Where 'Harry Potter' Was 
Filmed](https://www.ricksteves.com/watch-read-listen/read/articles/harry-potter-sites)
Source: Rick Steves Europe

Top Sights Where 'Harry Potter' Was Filmed · London · Near Bath · Near Brighton · Oxford · Durham and Northeast 
England · Scottish Highlands · Ireland.

2. [UK Harry Potter Filming Locations & 
Attractions](https://www.visitbritain.com/en/things-to-do/visit-harry-potter-filming-locations)
Source: VisitBritain

Harry Potter film locations around Britain · Freshwater West, Pembrokeshire, Wales · Lacock Abbey, Wiltshire, 
England · Alnwick Castle, Northumberland, England.

3. [31 Must Visit Harry Potter Filming Locations in the UK and 
...](https://flavourofthefilm.com/2024/11/01/31-must-visit-harry-potter-filming-locations-in-the-uk-and-ireland/)
Date published: Nov 1, 2024
Source: Flavour of the Film

Harry Potter Filming Locations: London · The Reptile House, London Zoo · Entrance to The Leaky Cauldron · Platform 
9 ¾, King's Cross Station.

4. [A Magical Guide to the Best Harry Potter Places to 
Visit](https://heleneinbetween.com/2025/03/harry-potter-filming-locations-best-places-to-travel-for-potterheads.htm
l)
Source: Helene in Between

From filming locations in England and Scotland, to unique places that look just like Diagon Alley, you need to 
travel here to experience the magic.

5. [Places in Harry Potter](https://en.wikipedia.org/wiki/Places_in_Harry_Potter)
Source: Wikipedia

The Leaky Cauldron · Diagon Alley · Knockturn Alley · Platform Nine and Three-Quarters · Hogsmeade · La Place 
Cachée, Paris.

6. [Harry Potter filming locations. Privet Dr, Dumbledore Island 
...](https://www.facebook.com/groups/3164534807204454/posts/4119439481713977/)
Source: Facebook · Film Locations - Then and Now

Harry Potter filming locations. Privet Dr, Dumbledore Island, The famous viaduct, The black lake, Hagrids Hut, 
Hogwarts, Harry & Hermione ...

7. [Harry Potter Filming Locations to Visit in 
Oxford](https://oxfordsummercourses.com/articles/harry-potter-filming-locations-in-oxford)
Date published: Apr 10, 2025
Source: Oxford Summer Courses

Explore the real-life Harry Potter filming locations across Oxford, from Hogwarts dining halls to secret corridors.

8. [Harry Potter Filming Locations in England](https://www.authenticvacations.com/harry-potter-filming-locations/)
Source: Authentic Vacations

Explore Hogwarts, Little Whinging, and more with this guide to Harry Potter Filming locations in England for the 
serious Harry Potter fan.

Out: None

[Step 1: Duration 7.65 seconds| Input tokens: 2,324 | Output tokens: 113]

...

━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ Step 4 ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

─ Executing parsed code: ──────────────────────────────────────────────────────────────────────────────────────── 
  import re                                                                                                        
  import pandas as pd                                                                                              
  from collections import defaultdict                                                                              
                                                                                                                   
  # Manual compilation of Harry Potter filming locations with their coordinates                                    
  locations_dict = {                                                                                               
      "Durham Cathedral": {"coords": (54.7791, -1.5787), "city": "Durham"},                                        
      "Alnwick Castle": {"coords": (55.0258, -1.5881), "city": "Alnwick"},                                         
      "Malham Cove, Skipton": {"coords": (54.1553, -1.9533), "city": "Skipton"},                                   
      "New College, Oxford": {"coords": (51.7495, -1.2472), "city": "Oxford"},                                     
      "Lacock Abbey": {"coords": (51.1858, -1.6266), "city": "Lacock"},                                            
      "Freshwater West, Pembrokeshire, Wales": {"coords": (51.7093, -4.9574), "city": "Pembrokeshire"},            
      "London": {"coords": (51.5074, -0.1278), "city": "London"},                                                  
      "King's Cross Station": {"coords": (51.5303, -0.1251), "city": "London"},                                    
      "Edinburgh Castles": {"coords": (55.9467, -3.1932), "city": "Edinburgh"},                                    
      "Glenfinnan Viaduct": {"coords": (56.6789, -5.4741), "city": "Glenfinnan"},                                  
      "Ireland": {"coords": (53.3478, -6.2597), "city": "Dublin"},                                                 
      

Execution logs:
                                 Location             Coordinates  \
0                        Durham Cathedral      (54.7791, -1.5787)   
1                          Alnwick Castle      (55.0258, -1.5881)   
2                    Malham Cove, Skipton      (54.1553, -1.9533)   
3                     New College, Oxford      (51.7495, -1.2472)   
4                            Lacock Abbey      (51.1858, -1.6266)   
5   Freshwater West, Pembrokeshire, Wales      (51.7093, -4.9574)   
6                                  London      (51.5074, -0.1278)   
7                    King's Cross Station      (51.5303, -0.1251)   
8                       Edinburgh Castles      (55.9467, -3.1932)   
9                      Glenfinnan Viaduct      (56.6789, -5.4741)   
10                                Ireland      (53.3478, -6.2597)   
11               Studio Borealis, Toronto     (43.8354, -79.4489)   
12                        London, Ontario     (42.9744, -81.2404)   
13                              Hogsmeade       (51.7631, 0.1849)   
14                 Paris, La Place Cachée       (48.8747, 2.3296)   
15                          Dunwich Heath   (52.111041, 1.705848)   
16                           York Minster       (53.9612, -1.087)   
17                    Leeds Train Station      (53.8013, -1.5477)   
18                             Derbyshire  (52.971686, -1.028428)   

    Travel Time to Pune (hours)   Nearby Cricket Stadiums  
0                         11.18  No cricket stadium found  
1                         11.19  No cricket stadium found  
2                         11.22  No cricket stadium found  
3                         11.15  No cricket stadium found  
4                         11.19  No cricket stadium found  
5                         11.50  No cricket stadium found  
6                         11.05  No cricket stadium found  
7                         11.05  No cricket stadium found  
8                         11.33  No cricket stadium found  
9                         11.52  No cricket stadium found  
10                        11.61  No cricket stadium found  
11                        18.28  No cricket stadium found  
12                        18.49  No cricket stadium found  
13                        11.02  No cricket stadium found  
14                        10.80  No cricket stadium found  
15                        10.87  No cricket stadium found  
16                        11.14  No cricket stadium found  
17                        11.18  No cricket stadium found  
18                        11.13  No cricket stadium found

Final answer:                                  Location             Coordinates  \
0                        Durham Cathedral      (54.7791, -1.5787)   
1                          Alnwick Castle      (55.0258, -1.5881)   
2                    Malham Cove, Skipton      (54.1553, -1.9533)   
3                     New College, Oxford      (51.7495, -1.2472)   
4                            Lacock Abbey      (51.1858, -1.6266)   
5   Freshwater West, Pembrokeshire, Wales      (51.7093, -4.9574)   
6                                  London      (51.5074, -0.1278)   
7                    King's Cross Station      (51.5303, -0.1251)   
8                       Edinburgh Castles      (55.9467, -3.1932)   
9                      Glenfinnan Viaduct      (56.6789, -5.4741)   
10                                Ireland      (53.3478, -6.2597)   
11               Studio Borealis, Toronto     (43.8354, -79.4489)   
12                        London, Ontario     (42.9744, -81.2404)   
13                              Hogsmeade       (51.7631, 0.1849)   
14                 Paris, La Place Cachée       (48.8747, 2.3296)   
15                          Dunwich Heath   (52.111041, 1.705848)   
16                           York Minster       (53.9612, -1.087)   
17                    Leeds Train Station      (53.8013, -1.5477)   
18                             Derbyshire  (52.971686, -1.028428)   

    Travel Time to Pune (hours)   Nearby Cricket Stadiums  
0                         11.18  No cricket stadium found  
1                         11.19  No cricket stadium found  
2                         11.22  No cricket stadium found  
3                         11.15  No cricket stadium found  
4                         11.19  No cricket stadium found  
5                         11.50  No cricket stadium found  
6                         11.05  No cricket stadium found  
7                         11.05  No cricket stadium found  
8                         11.33  No cricket stadium found  
9                         11.52  No cricket stadium found  
10                        11.61  No cricket stadium found  
11                        18.28  No cricket stadium found  
12                        18.49  No cricket stadium found  
13                        11.02  No cricket stadium found  
14                        10.80  No cricket stadium found  
15                        10.87  No cricket stadium found  
16                        11.14  No cricket stadium found  
17                        11.18  No cricket stadium found  
18                        11.13  No cricket stadium found  

[Step 4: Duration 107.13 seconds| Input tokens: 16,944 | Output tokens: 3,003]

In [12]:
result

Location             Coordinates  \
0                        Durham Cathedral      (54.7791, -1.5787)   
1                          Alnwick Castle      (55.0258, -1.5881)   
2                    Malham Cove, Skipton      (54.1553, -1.9533)   
3                     New College, Oxford      (51.7495, -1.2472)   
4                            Lacock Abbey      (51.1858, -1.6266)   
5   Freshwater West, Pembrokeshire, Wales      (51.7093, -4.9574)   
6                                  London      (51.5074, -0.1278)   
7                    King's Cross Station      (51.5303, -0.1251)   
8                       Edinburgh Castles      (55.9467, -3.1932)   
9                      Glenfinnan Viaduct      (56.6789, -5.4741)   
10                                Ireland      (53.3478, -6.2597)   
11               Studio Borealis, Toronto     (43.8354, -79.4489)   
12                        London, Ontario     (42.9744, -81.2404)   
13                              Hogsmeade       (51.7631, 0.1849)   
14                 Paris, La Place Cachée       (48.8747, 2.3296)   
15                          Dunwich Heath   (52.111041, 1.705848)   
16                           York Minster       (53.9612, -1.087)   
17                    Leeds Train Station      (53.8013, -1.5477)   
18                             Derbyshire  (52.971686, -1.028428)   

    Travel Time to Pune (hours)   Nearby Cricket Stadiums  
0                         11.18  No cricket stadium found  
1                         11.19  No cricket stadium found  
2                         11.22  No cricket stadium found  
3                         11.15  No cricket stadium found  
4                         11.19  No cricket stadium found  
5                         11.50  No cricket stadium found  
6                         11.05  No cricket stadium found  
7                         11.05  No cricket stadium found  
8                         11.33  No cricket stadium found  
9                         11.52  No cricket stadium found  
10                        11.61  No cricket stadium found  
11                        18.28  No cricket stadium found  
12                        18.49  No cricket stadium found  
13                        11.02  No cricket stadium found  
14                        10.80  No cricket stadium found  
15                        10.87  No cricket stadium found  
16                        11.14  No cricket stadium found  
17                        11.18  No cricket stadium found  
18                        11.13  No cricket stadium found

We could already improve this a bit by throwing in some dedicated planning steps, and adding more prompting.

In [ ]:
# Replacing qwen with gemini to run model with agent.planning_interval = 4 because qwen give API limit error
from smolagents import LiteLLMModel
model = LiteLLMModel(model_id="gemini/gemini-2.5-flash")
os.environ["GEMINI_API_KEY"] = ""

In [15]:
agent = CodeAgent(
    model=model,
    tools=[GoogleSearchTool(), VisitWebpageTool(), calculate_cargo_travel_time],
    additional_authorized_imports=["pandas"],
    max_steps=20,
)

In [32]:
agent.planning_interval = 4

detailed_report = agent.run(f"""
You're an expert analyst. You make comprehensive reports after visiting many websites.
Don't hesitate to search for many queries at once in a for loop.
For each data point that you find, visit the source url to confirm numbers.

{task}
""")

print(detailed_report)

╭──────────────────────────────────────────────────── New run ────────────────────────────────────────────────────╮
│                                                                                                                 │
│ You're an expert analyst. You make comprehensive reports after visiting many websites.                          │
│ Don't hesitate to search for many queries at once in a for loop.                                                │
│ For each data point that you find, visit the source url to confirm numbers.                                     │
│                                                                                                                 │
│ Find all Harry Potter filming locations in the world, calculate the time to transfer via passenger plane to     │
│ here (we're in Pune, 18.5204° N, 73.8567° E), and return them to me as a pandas dataframe.                      │
│ Also give me some cricket stadiums if there are any nearby to the filming locations                             │
│                                                                                                                 │
╰─ LiteLLMModel - gemini/gemini-2.5-flash ────────────────────────────────────────────────────────────────────────╯

ERROR:opentelemetry.exporter.otlp.proto.http.trace_exporter:Failed to export span batch code: 401, reason: {"message":"Invalid credentials. Confirm that you've configured the correct host."}


────────────────────────────────────────────────── Initial plan ───────────────────────────────────────────────────
Here are the facts I know and the plan of action that I will follow to solve the task:
```
## 1. Facts survey

### 1.1. Facts given in the task
*   **Origin location for travel time calculation:** Pune
*   **Pune's Latitude:** 18.5204° N
*   **Pune's Longitude:** 73.8567° E
*   **Desired travel mode:** Passenger plane
*   **Output format:** Pandas DataFrame
*   **Specific instruction:** Confirm numbers by visiting source URLs for each data point.

### 1.2. Facts to look up
*   **Harry Potter Filming Locations:**
    *   **Reasoning:** The core of the task is to find these locations. I need their names and details.
    *   **Source:** `web_search("Harry Potter filming locations list", "Harry Potter movie shooting sites")`
*   **Typical Cruising Speed of a Passenger Plane (km/h):**
    *   **Reasoning:** The `calculate_cargo_travel_time` tool has a default speed for cargo planes, but the task 
explicitly asks for "passenger plane" travel time. I need to find this specific value to override the default if 
necessary or confirm the default is suitable.
    *   **Source:** `web_search("typical passenger plane cruising speed km/h")`
*   **Geographical Coordinates (Latitude, Longitude) for each identified filming location:**
    *   **Reasoning:** The `calculate_cargo_travel_time` tool requires precise coordinates for both origin and 
destination. Once I have the names of the locations, I need to find their exact coordinates.
    *   **Source:** For each location `{location_name}`: `web_search("{location_name} coordinates latitude 
longitude")`
*   **Nearby Cricket Stadiums for each filming location:**
    *   **Reasoning:** The task specifically asks to list nearby cricket stadiums. I will need to perform a 
targeted search for each confirmed filming location.
    *   **Source:** For each location `{location_name}`: `web_search("cricket stadiums near {location_name}")`

### 1.3. Facts to derive
*   **Travel Time from Pune to each Harry Potter Filming Location:**
    *   **Reasoning:** This is a direct output required by the task, calculated using the 
`calculate_cargo_travel_time` tool, Pune's coordinates, each location's coordinates, and the passenger plane 
cruising speed.
*   **Structured Data (Pandas DataFrame):**
    *   **Reasoning:** The final output must be a pandas DataFrame. This will involve compiling all the collected 
and derived facts into a structured format with appropriate columns (e.g., Filming Location, Latitude, Longitude, 
Travel Time from Pune, Nearby Cricket Stadiums).

## 2. Plan

1.  **Determine Passenger Plane Cruising Speed:**
    *   Use `web_search` to find the typical cruising speed of a passenger plane in km/h. Store this value.
2.  **Identify Harry Potter Filming Locations and URLs:**
    *   Perform `web_search` for queries like "Harry Potter filming locations list", "Harry Potter actual shooting 
sites".
    *   Collect unique URLs from the search results that appear to contain lists or details of filming locations.
3.  **Extract Filming Locations and Confirm Details:**
    *   Initialize an empty list to store confirmed location data.
    *   For each collected URL:
        *   Use `visit_webpage` to get the content of the webpage.
        *   Parse the content to identify potential Harry Potter filming locations (names of places, landmarks, 
cities).
        *   For each potential location, perform `web_search` to confirm it is indeed a Harry Potter filming 
location and to find its precise latitude and longitude. Prioritize official or highly reputable sources for 
confirmation.
        *   Add the confirmed location name, its latitude, and its longitude to the list. Avoid duplicates.
4.  **Calculate Travel Time for each Location:**
    *   For each confirmed filming location in the list (with its coordinates):
        *   Call `calculate_cargo_travel_time` using Pune's coordinates 

━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ Step 1 ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

ERROR:opentelemetry.exporter.otlp.proto.http.trace_exporter:Failed to export span batch code: 401, reason: {"message":"Invalid credentials. Confirm that you've configured the correct host."}


...

ERROR:opentelemetry.exporter.otlp.proto.http.trace_exporter:Failed to export span batch code: 401, reason: {"message":"Invalid credentials. Confirm that you've configured the correct host."}


Error in generating model output:
litellm.RateLimitError: litellm.RateLimitError: geminiException - {
  "error": {
    "code": 429,
    "message": "You exceeded your current quota, please check your plan and billing details. For more information 
on this error, head to: https://ai.google.dev/gemini-api/docs/rate-limits. To monitor your current usage, head to: 
https://ai.dev/usage?tab=rate-limit.\n* Quota exceeded for metric: 
generativelanguage.googleapis.com/generate_content_free_tier_input_token_count, limit: 250000\nPlease retry in 
24.479631153s.",
    "status": "RESOURCE_EXHAUSTED",
    "details": [
      {
        "@type": "type.googleapis.com/google.rpc.QuotaFailure",
        "violations": [
          {
            "quotaMetric": "generativelanguage.googleapis.com/generate_content_free_tier_input_token_count",
            "quotaId": "GenerateContentInputTokensPerModelPerMinute-FreeTier",
            "quotaDimensions": {
              "location": "global",
              "model": "gemini-2.5-flash"
            },
            "quotaValue": "250000"
          }
        \]
      },
      {
        "@type": "type.googleapis.com/google.rpc.Help",
        "links": [
          {
            "description": "Learn more about Gemini API quotas",
            "url": "https://ai.google.dev/gemini-api/docs/rate-limits"
          }
        \]
      },
      {
        "@type": "type.googleapis.com/google.rpc.RetryInfo",
        "retryDelay": "24s"
      }
    ]
  }
}

ERROR:opentelemetry.exporter.otlp.proto.http.trace_exporter:Failed to export span batch code: 401, reason: {"message":"Invalid credentials. Confirm that you've configured the correct host."}


[Step 5: Duration 0.72 seconds]

AgentGenerationError: Error in generating model output:
litellm.RateLimitError: litellm.RateLimitError: geminiException - {
  "error": {
    "code": 429,
    "message": "You exceeded your current quota, please check your plan and billing details. For more information on this error, head to: https://ai.google.dev/gemini-api/docs/rate-limits. To monitor your current usage, head to: https://ai.dev/usage?tab=rate-limit.\n* Quota exceeded for metric: generativelanguage.googleapis.com/generate_content_free_tier_input_token_count, limit: 250000\nPlease retry in 24.479631153s.",
    "status": "RESOURCE_EXHAUSTED",
    "details": [
      {
        "@type": "type.googleapis.com/google.rpc.QuotaFailure",
        "violations": [
          {
            "quotaMetric": "generativelanguage.googleapis.com/generate_content_free_tier_input_token_count",
            "quotaId": "GenerateContentInputTokensPerModelPerMinute-FreeTier",
            "quotaDimensions": {
              "location": "global",
    

In [33]:
detailed_report

NameError: name 'detailed_report' is not defined

Thanks to these quick changes, we obtained a much more concise report by simply providing our agent a detailed prompt, and giving it planning capabilities!

💸 But as you can see, the context window is quickly filling up. So **if we ask our agent to combine the results of detailed search with another, it will be slower and quickly ramp up tokens and costs**.

➡️ We need to improve the structure of our system.

## ✌️ Splitting the task between two agents

Multi-agent structures allow to separate memories between different sub-tasks, with two great benefits:
- Each agent is more focused on its core task, thus more performant
- Separating memories reduces the count of input tokens at each step, thus reducing latency and cost.

Let's create a team with a dedicated web search agent, managed by another agent.

The manager agent should have plotting capabilities to redact its final report: so let us give it access to additional imports, including `plotly`, and `geopandas` + `shapely` for spatial plotting.

In [ ]:
os.environ["SERPER_API_KEY"] = "" # Changed to SERPER_API_KEY and getting from userdata
# os.environ["SERPAPI_API_KEY"] = ""

model = InferenceClientModel(
    "Qwen/Qwen2.5-Coder-32B-Instruct", provider="together", max_tokens=8096
)

web_agent = CodeAgent(
    model=model,
    tools=[
        GoogleSearchTool(provider="serper"),
        VisitWebpageTool(),
        calculate_cargo_travel_time,
    ],
    name="web_agent",
    description="Browses the web to find information",
    verbosity_level=0,
    max_steps=10,
)

The manager agent will need to do some mental heavy lifting.

So we give it the stronger model [DeepSeek-R1](https://huggingface.co/deepseek-ai/DeepSeek-R1), and add a `planning_interval` to the mix.

In [ ]:
# from google.colab import userdata
# import os
# os.environ["OPENAI_API_KEY"] = ""

In [ ]:
# from smolagents.utils import encode_image_base64, make_image_url
# from smolagents import OpenAIServerModel


# def check_reasoning_and_plot(final_answer, agent_memory):
#     multimodal_model = OpenAIServerModel("gpt-4o", max_tokens=8096)
#     filepath = "saved_map.png"
#     assert os.path.exists(filepath), "Make sure to save the plot under saved_map.png!"
#     image = Image.open(filepath)
#     prompt = (
#         f"Here is a user-given task and the agent steps: {agent_memory.get_succinct_steps()}. Now here is the plot that was made."
#         "Please check that the reasoning process and plot are correct: do they correctly answer the given task?"
#         "First list reasons why yes/no, then write your final decision: PASS in caps lock if it is satisfactory, FAIL if it is not."
#         "Don't be harsh: if the plot mostly solves the task, it should pass."
#         "To pass, a plot should be made using px.scatter_map and not any other method (scatter_map looks nicer)."
#     )
#     messages = [
#         {
#             "role": "user",
#             "content": [
#                 {
#                     "type": "text",
#                     "text": prompt,
#                 },
#                 {
#                     "type": "image_url",
#                     "image_url": {"url": make_image_url(encode_image_base64(image))},
#                 },
#             ],
#         }
#     ]
#     output = multimodal_model(messages).content
#     print("Feedback: ", output)
#     if "FAIL" in output:
#         raise Exception(output)
#     return True


# manager_agent = CodeAgent(

# model=OpenAIServerModel("gpt-4o", max_tokens=8096),
#    tools=[calculate_cargo_travel_time],
#     managed_agents=[web_agent],
#     additional_authorized_imports=[
#     "geopandas",
#     "plotly",
#     "plotly.io",  # explicitly add this
#     "plotly.express",  # explicitly add this too
#     "shapely",
#     "json",
#     "pandas",
#     "numpy",
#     "kaleido"
# ],
#     planning_interval=5,
#     verbosity_level=2,
#     final_answer_checks=[check_reasoning_and_plot],
#     max_steps=15,
# )

In [16]:
#not using openAI using gemini so commented above code
from smolagents.utils import encode_image_base64, make_image_url
# Import LiteLLMModel instead of OpenAIServerModel
from smolagents import LiteLLMModel


def check_reasoning_and_plot(final_answer, agent_memory):
    # Change to LiteLLMModel with a Gemini model ID
    multimodal_model = LiteLLMModel("gemini/gemini-2.5-flash", max_tokens=8096)
    filepath = "saved_map.png"
    assert os.path.exists(filepath), "Make sure to save the plot under saved_map.png!"
    image = Image.open(filepath)
    prompt = (
        f"Here is a user-given task and the agent steps: {agent_memory.get_succinct_steps()}. Now here is the plot that was made."
        "Please check that the reasoning process and plot are correct: do they correctly answer the given task?"
        "First list reasons why yes/no, then write your final decision: PASS in caps lock if it is satisfactory, FAIL if it is not."
        "Don't be harsh: if the plot mostly solves the task, it should pass."
        "To pass, a plot should be made using px.scatter_map and not any other method (scatter_map looks nicer)."
    )
    # The messages format is compatible for multimodal models
    messages = [
        {
            "role": "user",
            "content": [
                {
                    "type": "text",
                    "text": prompt,
                },
                {
                    "type": "image_url",
                    # LiteLLMModel (via LiteLLM) handles the image in the OpenAI message format
                    "image_url": {"url": make_image_url(encode_image_base64(image))},
                },
            ],
        }
    ]
    output = multimodal_model(messages).content
    print("Feedback: ", output)
    if "FAIL" in output:
        raise Exception(output)
    return True


manager_agent = CodeAgent(
    # Change to LiteLLMModel with a Gemini model ID
    model=LiteLLMModel("gemini/gemini-2.5-flash", max_tokens=8096),
    tools=[calculate_cargo_travel_time],
    managed_agents=[web_agent],
    additional_authorized_imports=[
    "geopandas",
    "plotly",
    "plotly.io",
    "plotly.express",
    "shapely",
    "json",
    "pandas",
    "numpy",
    "kaleido"
],
    planning_interval=5,
    verbosity_level=2,
    final_answer_checks=[check_reasoning_and_plot],
    max_steps=15,
)

Let us inspect what this team looks like:

In [17]:
manager_agent.visualize()

CodeAgent | gemini/gemini-2.5-flash
├── ✅ Authorized imports: ['geopandas', 'plotly', 'plotly.io', 'plotly.express', 'shapely', 'json', 'pandas', 
│   'numpy', 'kaleido']
├── 🛠️ Tools:
│   ┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
│   ┃ Name                        ┃ Description                           ┃ Arguments                             ┃
│   ┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│   │ calculate_cargo_travel_time │ Calculate the travel time for a cargo │ origin_coords (`array`): Tuple of     │
│   │                             │ plane between two points on Earth     │ (latitude, longitude) for the         │
│   │                             │ using great-circle distance.          │ starting point                        │
│   │                             │                                       │ destination_coords (`array`): Tuple   │
│   │                             │                                       │ of (latitude, longitude) for the      │
│   │                             │                                       │ destination                           │
│   │                             │                                       │ cruising_speed_kmh (`number`):        │
│   │                             │                                       │ Optional cruising speed in km/h       │
│   │                             │                                       │ (defaults to 750 km/h for typical     │
│   │                             │                                       │ cargo planes)                         │
│   │ final_answer                │ Provides a final answer to the given  │ answer (`any`): The final answer to   │
│   │                             │ problem.                              │ the problem                           │
│   └─────────────────────────────┴───────────────────────────────────────┴───────────────────────────────────────┘
└── 🤖 Managed agents:
    └── web_agent | CodeAgent | Qwen/Qwen2.5-Coder-32B-Instruct
        ├── ✅ Authorized imports: []
        ├── 📝 Description: Browses the web to find information
        └── 🛠️ Tools:
            ┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
            ┃ Name                        ┃ Description                       ┃ Arguments                         ┃
            ┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
            │ web_search                  │ Performs a google web search for  │ query (`string`): The search      │
            │                             │ your query then returns a string  │ query to perform.                 │
            │                             │ of the top search results.        │ filter_year (`integer`):          │
            │                             │                                   │ Optionally restrict results to a  │
            │                             │                                   │ certain year                      │
            │ visit_webpage               │ Visits a webpage at the given url │ url (`string`): The url of the    │
            │                             │ and reads its content as a        │ webpage to visit.                 │
            │                             │ markdown string. Use this to      │                                   │
            │                             │ browse webpages.                  │                                   │
            │ calculate_cargo_travel_time │ Calculate the travel time for a   │ origin_coords (`array`): Tuple of │
            │                             │ cargo plane between two points on │ (latitude, longitude) for the     │
            │                             │ Earth using great-circle          │ starting point                    │
           

In [18]:
!pip install markdownify requests
!pip install -U kaleido


manager_agent.run("""
Find all Harry Potter filming locations in the world, calculate the time to transfer via passenger plane to here (we're in Pune, 18.5204° N, 73.8567° E), and return them to me as a pandas dataframe.
Also give me some cricket stadiums if there are any nearby to the filming locations. You need at least 6 points in total.
Represent this as spatial map of the world, with the locations represented as scatter points with a color that depends on the travel time, and save it to saved_map.png!

Here's an example of how to plot and return a map:
import plotly.express as px
df = px.data.carshare()
fig = px.scatter_map(df, lat="centroid_lat", lon="centroid_lon", text="name", color="peak_hour", size=100,
     color_continuous_scale=px.colors.sequential.Magma, size_max=15, zoom=1)
fig.show()
fig.write_image("saved_image.png")
final_answer(fig)

Never try to process strings using code: when you have a string to read, just print it and you'll see it.
""")

╭──────────────────────────────────────────────────── New run ────────────────────────────────────────────────────╮
│                                                                                                                 │
│ Find all Harry Potter filming locations in the world, calculate the time to transfer via passenger plane to     │
│ here (we're in Pune, 18.5204° N, 73.8567° E), and return them to me as a pandas dataframe.                      │
│ Also give me some cricket stadiums if there are any nearby to the filming locations. You need at least 6 points │
│ in total.                                                                                                       │
│ Represent this as spatial map of the world, with the locations represented as scatter points with a color that  │
│ depends on the travel time, and save it to saved_map.png!                                                       │
│                                                                                                                 │
│ Here's an example of how to plot and return a map:                                                              │
│ import plotly.express as px                                                                                     │
│ df = px.data.carshare()                                                                                         │
│ fig = px.scatter_map(df, lat="centroid_lat", lon="centroid_lon", text="name", color="peak_hour", size=100,      │
│      color_continuous_scale=px.colors.sequential.Magma, size_max=15, zoom=1)                                    │
│ fig.show()                                                                                                      │
│ fig.write_image("saved_image.png")                                                                              │
│ final_answer(fig)                                                                                               │
│                                                                                                                 │
│ Never try to process strings using code: when you have a string to read, just print it and you'll see it.       │
│                                                                                                                 │
╰─ LiteLLMModel - gemini/gemini-2.5-flash ────────────────────────────────────────────────────────────────────────╯

────────────────────────────────────────────────── Initial plan ───────────────────────────────────────────────────
Here are the facts I know and the plan of action that I will follow to solve the task:
```
## 1. Facts survey

### 1.1. Facts given in the task
*   **Origin location for travel time calculation**: Pune, India.
*   **Coordinates of Pune**: Latitude 18.5204° N, Longitude 73.8567° E.
*   **Travel mode**: Passenger plane.
*   **Minimum total points required**: At least 6 points (filming locations + cricket stadiums).
*   **Desired output for locations and travel times**: Pandas DataFrame.
*   **Desired output for visualization**: Spatial map of the world (`saved_map.png`) using 
`plotly.express.scatter_map`.
*   **Map point representation**: Scatter points with color dependent on travel time.
*   **Map saving method**: `fig.write_image("saved_map.png")`.
*   **Final answer delivery method**: `final_answer(fig)`.

### 1.2. Facts to look up
*   **Harry Potter filming locations with coordinates**: We need a list of actual physical filming locations used 
for the Harry Potter movies (not just fictional settings) and their precise latitude and longitude coordinates.
    *   **Source**: Web search using `web_agent`. Example search query: "Harry Potter filming locations 
coordinates".
*   **Coordinates of cricket stadiums**: We need to identify a few cricket stadiums that can be considered "nearby"
to some of the found Harry Potter filming locations, along with their names and coordinates (latitude and 
longitude). The number of stadiums needed will depend on how many filming locations are found to meet the minimum 
of 6 points.
    *   **Source**: Web search using `web_agent`. Example search query: "cricket stadiums near [specific filming 
location name] coordinates". This will likely be an iterative lookup after filming locations are identified.
*   **Typical cruising speed of a passenger plane**: The `calculate_cargo_travel_time` tool has an optional 
`cruising_speed_kmh` argument that defaults to 750 km/h for cargo planes. Since the task explicitly asks for 
"passenger plane", we should use a more appropriate speed for passenger aircraft.
    *   **Source**: Web search using `web_agent`. Example search query: "typical cruising speed commercial 
passenger jet km/h". We will use 900 km/h unless the lookup suggests a significantly different common value.

### 1.3. Facts to derive
*   **List of Harry Potter filming locations with structured data**: This will involve extracting names, latitudes,
and longitudes from the web search results.
*   **Travel time from Pune to each Harry Potter filming location**: This will be computed using the 
`calculate_cargo_travel_time` tool for each identified location, using Pune's coordinates as the origin and a 
typical passenger plane speed.
*   **List of selected cricket stadiums with structured data**: This will involve extracting names, latitudes, and 
longitudes from the web search results for stadiums found near filming locations.
*   **Travel time from Pune to each selected cricket stadium**: This will be computed using the 
`calculate_cargo_travel_time` tool for each identified stadium, using Pune's coordinates as the origin and a 
typical passenger plane speed.
*   **Combined Pandas DataFrame**: A single DataFrame containing all chosen Harry Potter filming locations and 
cricket stadiums, with columns for location name, latitude, longitude, travel time from Pune, and a categorical 
'Type' column (e.g., 'HP Filming Location', 'Cricket Stadium').
*   **Plotly Figure object**: A `plotly.express.scatter_map` figure generated from the combined DataFrame, 
visualizing the locations, colored by travel time, which will be saved and returned.

## 2. Plan

1.  Use `web_agent` to find a list of prominent Harry Potter filming locations along with their latitude and 
longitude coordinates.
2.  Process the results from the `web_agent` to extract at least 4-5 Harry Potter filming locations, stor

━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ Step 1 ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

Output message of the LLM: ────────────────────────────────────────────────────────────────────────────────────────
<code>                                                                                                             
hp_locations_raw = web_agent(                                                                                      
    task="Find prominent Harry Potter filming locations with their precise latitude and longitude coordinates.     
Prioritize well-known locations that are distinct from each other and clearly tied to specific movie scenes.       
Provide the name, latitude, and longitude for at least 5-7 locations.",                                            
    additional_args={}                                                                                             
)                                                                                                                  
print(hp_locations_raw)                                                                                            
                                                                                                                   

─ Executing parsed code: ──────────────────────────────────────────────────────────────────────────────────────── 
  hp_locations_raw = web_agent(                                                                                    
      task="Find prominent Harry Potter filming locations with their precise latitude and longitude coordinates.   
  Prioritize well-known locations that are distinct from each other and clearly tied to specific movie scenes.     
  Provide the name, latitude, and longitude for at least 5-7 locations.",                                          
      additional_args={}                                                                                           
  )                                                                                                                
  print(hp_locations_raw)                                                                                          
 ─────────────────────────────────────────────────────────────────────────────────────────────────────────────────

...

Check check_reasoning_and_plot failed with error: Make sure to save the plot under saved_map.png!

[Step 15: Duration 11.87 seconds| Input tokens: 439,835 | Output tokens: 25,491]

Reached max steps.

[Step 16: Duration 15.37 seconds| Input tokens: 502,496 | Output tokens: 27,442]

'```python\nimport pandas as pd\nimport plotly.express as px\nimport numpy as np\n\n# Pune coordinates\nPUNE_COORDS = (18.5204, 73.8567)\nPASSENGER_PLANE_SPEED_KMH = 900 # A typical cruising speed for a commercial passenger jet\n\n# Harry Potter filming locations with their coordinates (pre-defined due to web_agent limitations)\nhp_filming_locations = [\n    {"Name": "Alnwick Castle", "latitude": 55.4158, "longitude": -1.7058, "Type": "Harry Potter Filming Location"},\n    {"Name": "Durham Cathedral", "latitude": 54.7738, "longitude": -1.5768, "Type": "Harry Potter Filming Location"},\n    {"Name": "Glenfinnan Viaduct", "latitude": 56.8778, "longitude": -5.4326, "Type": "Harry Potter Filming Location"},\n    {"Name": "Warner Bros. Studio Tour London", "latitude": 51.6908, "longitude": -0.4190, "Type": "Harry Potter Filming Location"},\n    {"Name": "King\'s Cross Station", "latitude": 51.5308, "longitude": -0.1227, "Type": "Harry Potter Filming Location"},\n]\n\n# Calculate travel time

In [19]:
manager_agent.python_executor.state["fig"]